In [2]:
import numpy as np
import pandas as pd

import matplotlib.pyplot as plt
import plotly.graph_objects as go
from plotly.subplots import make_subplots

from scipy.integrate import cumulative_trapezoid, solve_ivp, quad
from scipy.interpolate import interp1d
from scipy.special import genlaguerre, sph_harm, factorial

from field_functions import LaserField



class AU:
    meter = 5.2917720859e-11 # atomic unit of length in meters
    nm = 5.2917721e-2 # atomic unit of length in nanometres
    second = 2.418884328e-17 # atomic unit of time in seconds
    fs = 2.418884328e-2 # atomic unit of time in femtoseconds
    Joule = 4.359743935e-18 # atomic unit of energy in Joules
    eV = 27.21138383 # atomic unit of energy in electronvolts
    Volts_per_meter = 5.142206313e+11 # atomic unit of electric field in V/m
    Volts_per_Angstrom = 51.42206313 # atomic unit of electric field in V/Angström
    speed_of_light = 137.035999 # vacuum speed of light in atomic units
    Coulomb = 1.60217646e-19 # atomic unit of electric charge in Coulombs
    PW_per_cm2_au = 0.02849451308 # PW/cm^2 in atomic units
AtomicUnits=AU

class HydrogenState:
    def __init__(self, n, l, m):
        if not (n > 0 and 0 <= l < n and -l <= m <= l):
            raise ValueError("Invalid quantum numbers")
        self.n = n
        self.l = l
        self.m = m
    @property
    def energy(self): return -0.5 / (self.n**2)
    def __repr__(self): return f"|{self.n},{self.l},{self.m}>"
    def __eq__(self, other): return self.n == other.n and self.l == other.l and self.m == other.m
    def __hash__(self): return hash((self.n, self.l, self.m))

def R_nl_func(r, n, l):
    if l >= n: return np.zeros_like(r)
    coeff = np.sqrt((2.0/n)**3 * factorial(n-l-1) / (2.0*n*factorial(n+l)))
    laguerre_poly = genlaguerre(n-l-1, 2*l+1)
    return coeff * np.exp(-r/n) * (2.0*r/n)**l * laguerre_poly(2.0*r/n)

_radial_integral_cache = {}
def radial_integral_z(n1, l1, n2, l2):
    key = tuple(sorted(((n1, l1), (n2, l2))))
    if key in _radial_integral_cache: return _radial_integral_cache[key]
    integrand = lambda r: R_nl_func(r, n1, l1) * r * R_nl_func(r, n2, l2) * r**2
    max_n_involved = max(n1, n2)
    r_max_integration = 2.5 * max_n_involved**2 + 40
    if l1 >= n1 or l2 >= n2: return 0.0
    result, error = quad(integrand, 0, r_max_integration, limit=200, epsabs=1e-9, epsrel=1e-9)
    _radial_integral_cache[key] = result
    return result

def angular_integral_z(l1, m1, l2, m2):
    if m1 != m2: return 0.0
    if abs(l1 - l2) != 1: return 0.0
    if l1 == l2 + 1: l, m = l2, m2; return np.sqrt(((l+1)**2 - m**2) / ((2*l+1)*(2*l+3)))
    elif l1 == l2 - 1: l, m = l2, m2; return np.sqrt((l**2 - m**2) / ((2*l-1)*(2*l+1)))
    return 0.0

_z_matrix_element_cache = {}
def z_matrix_element(state1: HydrogenState, state2: HydrogenState):
    key = tuple(sorted((state1, state2), key=lambda s: (s.n, s.l, s.m)))
    if key in _z_matrix_element_cache: return _z_matrix_element_cache[key]
    if state1.m != state2.m: _z_matrix_element_cache[key] = 0.0; return 0.0
    rad_int = radial_integral_z(state1.n, state1.l, state2.n, state2.l)
    ang_int = angular_integral_z(state1.l, state1.m, state2.l, state2.m)
    result = rad_int * ang_int
    _z_matrix_element_cache[key] = result
    return result

def extract_time(file_path):
    with open(file_path, 'r') as file:
        first_colomn = []
        for row, line in enumerate(file):
            if row < 6:
                continue
            line = line.strip()
            colomns = line.split()
            if len(colomns) >= 5:
                first_colomn.append(float(colomns[0]))
    return first_colomn

def extractField_0(file_path):
    with open(file_path, 'r') as file:
        fifth_colomn = []
        for row, line in enumerate(file):
            if row < 6:
                continue
            line = line.strip()
            colomns = line.split()
            if len(colomns) >= 5:
                fifth_colomn.append(float(colomns[5]))
    return fifth_colomn

# Laser dense

In [11]:
df_dense=pd.read_csv("/home/user/BachelorThesis/trecxcoefftests/tiptoe_dense/0021/expec", sep='\s+', header=8)
#shift every column name by one and remove the first column
df_dense.columns = df_dense.columns[1:].tolist() + [""]
#remove last column
df_dense = df_dense.iloc[:, :-1]




fig = go.Figure()
#fig.add_trace(go.Scatter(x=np.array(df_dense["Time"]), y=np.array(np.imag(c)), mode='lines', name='c^2_Occ_0'))
#fig.add_trace(go.Scatter(x=np.array(df_dense["Time"]), y=np.array(df_dense["Re{<H0:0|psi>}"]), mode='lines', name='c^2_new'))
fig.add_trace(go.Scatter(x=np.array(df_dense["Time"]), y=np.array(df_dense["<Occ{H0:1}>"]), mode='lines', name='c^2_Occ_1'))
fig.add_trace(go.Scatter(x=np.array(df_dense["Time"]), y=np.array(df_dense["<Occ{H0:2}>"]), mode='lines', name='c^2_Occ_2'))
fig.add_trace(go.Scatter(x=np.array(df_dense["Time"]), y=np.array(df_dense["<Occ{H0:3}>"]), mode='lines', name='c^2_Occ_3'))
fig.add_trace(go.Scatter(x=np.array(df_dense["Time"]), y=np.array(df_dense["<Occ{H0:4}>"]), mode='lines', name='c^2_Occ_4'))
fig.add_trace(go.Scatter(x=np.array(df_dense["Time"]), y=np.array(df_dense["<Occ{H0:5}>"]), mode='lines', name='c^2_Occ_5'))
#fig.add_trace(go.Scatter(x=np.array(df_dense["Time"]), y=1-(np.real(cumulative_integral_reduced)**2+np.imag(cumulative_integral_reduced)**2), mode='lines', name='c^2_analytical'))
#fig.add_trace(go.Scatter(x=np.array(df_dense["Time"]), y=np.array(df_dense["Re{<H0:2|psi>}"]**2+df_dense["Imag{<H0:2|psi>}"]**2), mode='lines', name='c^2_new'))
#fig.add_trace(go.Scatter(x=np.array(df_dense["Time"]), y=np.array(df_dense["Re{<H0:0|psi>}"]), mode='lines', name='c^2_new'))

tRecX outputs the coefficients in ordners of energy level, so $1s->2s->2p->3s->3p->4s->3d->...$. But we know that i.e. $1s->2s$ is forbidden, so $l$ needs to change. Thats why $c^2_3$ and $c^2_5$ are far below the others. $c^2_2$ and $c^2_4$ can both be accessed by a normal dipole transition However $c^2_1$ is normally not possible to access but nevertheless its propability is the highest because of multiphotonprocesses.

# Analytical coefficients

Analytical calculation of ground state coefficient compared to tRecX

In [3]:
time0 = extract_time("/home/user/BachelorThesis/trecxcoefftests/tiptoe_dense/0013/Laser")
field0 = extractField_0("/home/user/BachelorThesis/trecxcoefftests/tiptoe_dense/0013/Laser")

integrand = np.exp(1j* 1/2 * np.array(time0)) * np.array(field0) #* np.exp(-1j* 1/2 * np.array(time0)) #because of interaction representation
cumulative_integral = cumulative_trapezoid(-1j*integrand, x=np.array(time0), initial=0)
interp_func = interp1d(time0, cumulative_integral, kind='cubic', fill_value="extrapolate")
cumulative_integral_reduced = interp_func(df_dense["Time"]) #* np.exp(+1j* 1/4 * df_dense["Time"])

test = (df_dense["Re{<H0:0|psi>}"]+1j*df_dense["Imag{<H0:0|psi>}"])#* np.exp(-1j* 1/1 * df_dense["Time"])

fig = go.Figure()
fig.add_trace(go.Scatter(x=np.array(df_dense["Time"]), y=np.array(df_dense["<Occ{H0:1}>"]), mode='lines', name='c^2_Occ_new'))
#fig.add_trace(go.Scatter(x=np.array(df_dense["Time"]), y=np.array(np.imag(test)), mode='lines', name='c^2_Occ_new'))
#fig.add_trace(go.Scatter(x=np.array(df_dense["Time"]), y=1-(np.real(cumulative_integral_reduced)**2+np.imag(cumulative_integral_reduced)**2), mode='lines', name='c^2_analytical'))

#fig.add_trace(go.Scatter(x=np.array(df_dense["Time"]), y=np.imag(cumulative_integral_reduced), mode='lines', name='c^2_analytical'))
#fig.add_trace(go.Scatter(x=np.array(df_dense["Time"]), y=np.array(df_dense["Re{<H0:0|psi>}"])**2+np.array(df_dense["Imag{<H0:0|psi>}"])**2, mode='lines', name='c^2_Occ_new'))

WRONG!!
Physical measurements have to be the same in both schroedinger and interaction picture so $c^2$ has to be equal. When switching from schroedinger to interaction picture, the real part of the coefficients are zero, all the oszillation in the $c^2$ are in the imaginary part. However in the schroedinger picture both parts are giving an equal contribution to the propability amplitude. The schroedinger picture is somewhat more physically intuitive because at $t=0$ the propability amplitude of an electron sitting in ground state is at its lowest because the laser has its peak there. 
The coefficients in interaction picture are giving by $c_n^I(t)=e^{iE_nt}c_n(t)$.
The discrepancy between the two graphs is due to the fact that in the analytical calculation I assumed that the occupation of the ground state is approx $1$ and the occupation of the excited states is sufficiently small.

In [ ]:
integral_of_field = cumulative_trapezoid(field0, time0, initial=0)

field_interp = interp1d(time0, integral_of_field, kind='cubic', fill_value="extrapolate")

def A(t):
    F = -field_interp(t)
    return np.array([[-1j*F, -1j*F*np.exp(-1j*t*0), -1j*F*np.exp(1j*t*0.25)],
                     [-1j*F*np.exp(1j*t*0), -1j*F, -1j*F*np.exp(1j*t*0.25)],
                     [-1j*F*np.exp(-1j*t*0.25), -1j*F*np.exp(-1j*t*0.25), -1j*F]])

y0 = np.array([1+0j, 0+0j, 0+0j])

def rhs(t, y):
    return A(t) @ y


sol = solve_ivp(rhs, [time0[0], time0[-1]], y0, t_eval=time0)
solution = sol.y*np.exp(-1j*1/6*sol.t)



fig = go.Figure()

#fig.add_trace(go.Scatter(x=np.array(time0), y=np.real(solution[1]), mode='lines', name='analytical'))
#fig.add_trace(go.Scatter(x=np.array(time0), y=np.abs(solution[0])**2, mode='lines', name='c_analytical'))
#fig.add_trace(go.Scatter(x=np.array(time0), y=np.abs(sol.y[2])**2, mode='lines', name='c^2_Occ_2'))

#fig.add_trace(go.Scatter(x=np.array(df_dense["Time"]), y=np.array(df_dense["<Occ{H0:1}>"]), mode='lines', name='c^2_Occ_0'))
#fig.add_trace(go.Scatter(x=np.array(df_dense["Time"]), y=np.array(df_dense["Re{<H0:1|psi>}"]), mode='lines', name='c_trecx'))
#fig.add_trace(go.Scatter(x=np.array(df_dense["Time"]), y=np.array(df_dense["Imag{<H0:1|psi>}"]), mode='lines', name='c_trecximag'))


coeff = np.array(df_dense["Re{<H0:2|psi>}"]) + 1j*np.array(df_dense["Imag{<H0:2|psi>}"])
coeffInteraction = coeff*np.exp(+1j*1/8*df_dense["Time"])

fig.add_trace(go.Scatter(x=np.array(df_dense["Time"]), y=np.real(coeffInteraction), mode='lines', name='trecx_schroedinger'))




In [22]:
file_params = [
    ("450nm_1e+14", 450, 1e14, 350, 1e10, 1, 0, 0),
]


df_verify=pd.read_csv("/home/user/BachelorThesis/trecxcoefftests/tiptoe_dense/0021/expec", sep='\s+', header=8)
df_verify.columns = df_verify.columns[1:].tolist() + [""]
df_verify = df_verify.iloc[:, :-1]



for file_name, lam0_pump, I_pump, lam0_probe, I_probe, FWHM_probe, cep_pump, cep_probe in file_params:
    laser_pulses = LaserField(cache_results=True)
    laser_pulses.add_pulse(lam0_pump, I_pump, cep_pump, lam0_pump/ AtomicUnits.nm / AtomicUnits.speed_of_light)
    t_min, t_max = laser_pulses.get_time_interval()
    time_recon= np.arange(t_min, t_max+1, 1)





# --- Basis Set ---
basis_states = []
max_n_basis = 3
for n_val in range(1, max_n_basis + 1):
    for l_val in range(n_val):
        m_val = 0
        basis_states.append(HydrogenState(n_val, l_val, m_val))
num_states = len(basis_states)
print(f"Basis states ({num_states}): {basis_states}")

E_j = np.array([s.energy for s in basis_states])
z_jk_matrix = np.zeros((num_states, num_states))
for j, state_j in enumerate(basis_states):
    for k, state_k in enumerate(basis_states):
        if j <= k:
            val = z_matrix_element(state_j, state_k)
            z_jk_matrix[j, k] = val
            z_jk_matrix[k, j] = val

# --- 4. Coupled ODEs ---
def tdse_rhs(t, y_complex):
    c = y_complex[:-1]
    A_z_val = y_complex[-1].real
    dc_dt = np.zeros_like(c, dtype=np.complex128)
    #E_field_t = E_z_laser(t)
    E_field_t = laser_pulses.Electric_Field(t)
    for k_idx in range(num_states):
        sum_val = 0.0j
        for n_idx in range(num_states):
            if k_idx == n_idx: continue
            z_kn = z_jk_matrix[k_idx, n_idx]
            if z_kn == 0: continue
            phase_factor = np.exp(1j * (E_j[k_idx] - E_j[n_idx]) * t)
            term = c[n_idx] * (E_j[k_idx] - E_j[n_idx]) * z_kn * phase_factor
            sum_val += term
        dc_dt[k_idx] = sum_val * A_z_val
    dA_z_dt = -E_field_t
    derivatives = np.append(dc_dt, dA_z_dt)
    return derivatives

# --- 5. Numerical Solution ---
s1_state = HydrogenState(1,0,0)
idx_1s = basis_states.index(s1_state)
c_initial = np.zeros(num_states, dtype=np.complex128)
c_initial[idx_1s] = 1.0 + 0.0j
A_z_initial = 0.0
y0_complex = np.append(c_initial, A_z_initial)

t_start, t_end = laser_pulses.get_time_interval()
num_t_points = 500
t_eval_points = np.linspace(t_start, t_end, num_t_points*32)

sol = solve_ivp(tdse_rhs, [t_start, t_end], y0_complex, t_eval=t_eval_points,
                method='BDF', rtol=1e-10, atol=1e-10, max_step=0.5) # Consider BDF or LSODA for long times if stiff




# --- Plotting Results with Plotly ---


fig_pops = go.Figure()
for i in range(1, num_states):#numStates 
    fig_pops.add_trace(go.Scatter(x=sol.t, y=np.abs(sol.y[i, :])**2, mode='lines', name=f'Pop. {basis_states[i]}'))

    coeff = np.array(df_verify[f"Re{{<H0:{i}|psi>}}"]) + 1j*np.array(df_verify[f"Imag{{<H0:{i}|psi>}}"])
    coeffInteraction = coeff#*np.exp(+1j*1/8*df_dense["Time"])

    #coeff_interp = interp1d(df_verify["Time"], coeffInteraction, kind='cubic', fill_value="extrapolate")
    
    #fig_pops.add_trace(go.Scatter(x=sol.t, y=np.abs(coeff_interp(sol.t))**2, mode='lines', name=f'trecx. {basis_states[i]}'))


fig_pops.update_layout(
    xaxis_title="Time (atomic units)",
    yaxis_title="Population |c<sub>k</sub>(t)|<sup>2</sup>",
    xaxis_range=[-200, 200],
    legend_title="States"
)



fig_pops.show()

Basis states (6): [|1,0,0>, |2,0,0>, |2,1,0>, |3,0,0>, |3,1,0>, |3,2,0>]


In [15]:
df_dense=pd.read_csv("/home/user/BachelorThesis/trecxcoefftests/tiptoe_dense/0021/expec", sep='\s+', header=8)
#shift every column name by one and remove the first column
df_dense.columns = df_dense.columns[1:].tolist() + [""]
#remove last column
df_dense = df_dense.iloc[:, :-1]




fig = go.Figure()
#fig.add_trace(go.Scatter(x=np.array(df_dense["Time"]), y=np.array(np.imag(c)), mode='lines', name='c^2_Occ_0'))
#fig.add_trace(go.Scatter(x=np.array(df_dense["Time"]), y=np.array(df_dense["Re{<H0:0|psi>}"]), mode='lines', name='c^2_new'))
fig.add_trace(go.Scatter(x=np.array(df_dense["Time"]), y=np.array(df_dense["<Occ{H0:1}>"]), mode='lines', name='c^2_Occ_1'))
fig.add_trace(go.Scatter(x=np.array(df_dense["Time"]), y=np.array(df_dense["<Occ{H0:2}>"]), mode='lines', name='c^2_Occ_2'))
fig.add_trace(go.Scatter(x=np.array(df_dense["Time"]), y=np.array(df_dense["<Occ{H0:3}>"]), mode='lines', name='c^2_Occ_3'))
fig.add_trace(go.Scatter(x=np.array(df_dense["Time"]), y=np.array(df_dense["<Occ{H0:4}>"]), mode='lines', name='c^2_Occ_4'))
fig.add_trace(go.Scatter(x=np.array(df_dense["Time"]), y=np.array(df_dense["<Occ{H0:5}>"]), mode='lines', name='c^2_Occ_5'))
#fig.add_trace(go.Scatter(x=np.array(df_dense["Time"]), y=1-(np.real(cumulative_integral_reduced)**2+np.imag(cumulative_integral_reduced)**2), mode='lines', name='c^2_analytical'))
#fig.add_trace(go.Scatter(x=np.array(df_dense["Time"]), y=np.array(df_dense["Re{<H0:2|psi>}"]**2+df_dense["Imag{<H0:2|psi>}"]**2), mode='lines', name='c^2_new'))
#fig.add_trace(go.Scatter(x=np.array(df_dense["Time"]), y=np.array(df_dense["Re{<H0:0|psi>}"]), mode='lines', name='c^2_new'))